<a href="https://colab.research.google.com/github/HemantKArya/MIDI_Mamba/blob/main/MIDI_Mamba.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# @title # Install Libs
!pip install pretty_midi midi2audio
!pip install miditok

!apt-get install fluidsynth

!pip install causal-conv1d>=1.1.0
!pip install mamba-ssm

!export LC_ALL="en_US.UTF-8"
!export LD_LIBRARY_PATH="/usr/lib64-nvidia"
!export LIBRARY_PATH="/usr/local/cuda/lib64/stubs"
!ldconfig /usr/lib64-nvidia

In [ ]:
import torch
from mamba_ssm import Mamba
from mamba_ssm.models.mixer_seq_simple import MambaLMHeadModel
from mamba_ssm.models.config_mamba import MambaConfig
import numpy as np

In [ ]:
from midi2audio import FluidSynth
import IPython.display as ipd
fs = FluidSynth()

In [ ]:
!wget https://huggingface.co/krystv/MIDI_Mamba-159M/resolve/main/MIDI_Mamba-159M_1536VS.pt
!wget https://huggingface.co/krystv/MIDI_Mamba-159M/resolve/main/tokenizer_1536mix_BPE.json

In [ ]:
mc = MambaConfig()
mc.d_model = 768
mc.n_layer = 42
mc.vocab_size = 1536

In [ ]:
import IPython
import pretty_midi

In [ ]:
from miditok import MIDILike,REMI,TokenizerConfig
from pathlib import Path

tokenizer = REMI(params='tokenizer_1536mix_BPE.json')

In [ ]:
mf = MambaLMHeadModel(config=mc,device='cuda:0')
mf.load_state_dict(torch.load("/content/MIDI_Mamba-159M_1536VS.pt",map_location='cuda:0'))

<All keys matched successfully>

In [ ]:
input_ids = torch.tensor([[1,]]).to('cuda:0')

out = mf.generate(
    input_ids=input_ids,
    max_length=512,
    temperature=0.9,
    top_p=0.9,
    top_k=30,

    eos_token_id=2,
)
m = tokenizer.decode(np.array(out[0].to('cpu')))
np.array(out.to('cpu')).shape
m.dump_midi('output.mid')

In [ ]:
fs.midi_to_audio('output.mid', 'output.wav')
ipd.Audio("output.wav")

In [ ]:
def count_parameters(model):
    total_params = sum(p.numel() for p in model.parameters())
    return total_params

count_parameters(mf)

159589632